In [1]:
import pandas as pd
import numpy as np
import os
import sumolib
import random
from tqdm import tqdm
from datetime import datetime

# A. 이동류 매칭

In [2]:
# [이동류번호] 불러오기 (약 1분의 소요시간)
path_moves = '../../Data/tables/moves/'
csv_moves = os.listdir('../../Data/tables/moves/')
moves = [pd.read_csv(path_moves + csv_move, index_col=0) for csv_move in tqdm(csv_moves)]
match1 = pd.concat(moves).drop_duplicates().sort_values(by=['inter_no','phas_A','phas_B']).reset_index(drop=True)
match1.head(10)

  0%|          | 15/17280 [00:00<01:56, 148.29it/s]

100%|██████████| 17280/17280 [01:11<00:00, 242.06it/s]


inter_no  phas_A  phas_B  move_A  move_B
0       175       1       1       8       4
1       175       2       2       7       3
2       175       3       3       6       1
3       175       3       4       6       2
4       175       4       4       5       2
5       176       1       1       8       4
6       176       2       2       8       3
7       176       3       3       5      18
8       177       1       1       8       4
9       177       2       2       7       3

In [3]:
# 계층화 (inter_no, phas_A, phas_B, move_A, move_B) -> ('inter_no', 'phase_no', 'ring_type', 'move_no')
matchA = match1[['inter_no', 'phas_A', 'move_A']].copy()
matchA.columns = ['inter_no', 'phase_no', 'move_no']
matchA['ring_type'] = 'A'
matchB = match1[['inter_no', 'phas_B', 'move_B']].copy()
matchB.columns = ['inter_no', 'phase_no', 'move_no']
matchB['ring_type'] = 'B'
match2 = pd.concat([matchA, matchB]).drop_duplicates()
match2 = match2[['inter_no', 'phase_no', 'ring_type', 'move_no']]
match2 = match2.sort_values(by=list(match2.columns))
match2.head(10)

inter_no  phase_no ring_type  move_no
0       175         1         A        8
0       175         1         B        4
1       175         2         A        7
1       175         2         B        3
2       175         3         A        6
2       175         3         B        1
4       175         4         A        5
3       175         4         B        2
5       176         1         A        8
5       176         1         B        4

In [4]:
# [nema 이동류목록] 불러오기 및 병합
nema = pd.read_csv('../../Data/tables/nema.csv', encoding='cp949')
match3 = pd.merge(match2, nema, how='left', on='move_no').drop_duplicates()
match3

inter_no  phase_no ring_type  move_no inc_dir out_dir
0        175         1         A        8       남       북
1        175         1         B        4       북       남
2        175         2         A        7       북       동
3        175         2         B        3       남       서
4        175         3         A        6       동       서
5        175         3         B        1       동       남
6        175         4         A        5       서       북
7        175         4         B        2       서       동
8        176         1         A        8       남       북
9        176         1         B        4       북       남
10       176         2         A        8       남       북
11       176         2         B        3       남       서
12       176         3         A        5       서       북
13       176         3         B       18     NaN     NaN
14       177         1         A        8       남       북
15       177         1         B        4       북       남
16       177         2         A        7       북       동
17       177         2         B        3       남       서
18       177         3         A       17     NaN     NaN
19       177         3         B       18     NaN     NaN
20       177         4         A        5       서       북
21       177         4         B        1       동       남
22       178         1         A        8       남       북
23       178         1         B        4       북       남
24       178         2         A        7       북       동
25       178         2         B        3       남       서
26       178         3         A        5       서       북
27       178         3         B        2       서       동
28       178         4         A        6       동       서
29       178         4         B        1       동       남
30       201         1         A        8       남       북
31       201         1         B        3       남       서
32       201         2         A        5       서       북
33       201         2         B        2       서       동
34       201         3         A        6       동       서
35       201         3         B        2       서       동
36       201         4         A        6       동       서
37       201         4         B        1       동       남
38       201         5         A        7       북       동
39       201         5         B        4       북       남
40       202         1         A        6       동       서
41       202         1         B        2       서       동
42       202         2         A       17     NaN     NaN
43       202         2         B       18     NaN     NaN
44       206         1         A        8       남       북
45       206         1         B        4       북       남
46       206         2         A       17     NaN     NaN
47       206         2         B       18     NaN     NaN
48       206         3         A        8       남       북
49       206         3         B        4       북       남
50       206         4         A       17     NaN     NaN
51       206         4         B       18     NaN     NaN
52       210         1         A        6       동       서
53       210         1         B       18     NaN     NaN
54       210         2         A        5       서       북
55       210         2         B        2       서       동
56       210         3         A        7       북       동
57       210         3         B        4       북       남
58       210         4         A        8       남       북
59       210         4         B        3       남       서

In [5]:
# [방위각정보] 불러오기, 계층화, 병합
# 불러오기
dtype_dict = {f'angle_{alph}{j}':'str' for alph in ['A', 'B'] for j in range(1,9)}
angle_original = pd.read_csv('../../Data/tables/angle.csv', index_col=0, dtype = dtype_dict)
# 계층화
angle = []
for i, row in angle_original.iterrows():
    angle_codes = row[[f'angle_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
    new = pd.DataFrame({'inter_no':[row.inter_no] * 16, 'phase_no':list(range(1, 9))*2, 'ring_type':['A'] * 8 + ['B'] * 8, 'angle_code':angle_codes.to_list()})
    angle.append(new)
angle = pd.concat(angle)
angle = angle.dropna().reset_index(drop=True)
# 병합
six_chars = angle.angle_code.apply(lambda x:len(x)==6)
angle.loc[six_chars,'inc_angle'] = angle.angle_code.apply(lambda x:x[:3])
angle.loc[six_chars,'out_angle'] = angle.angle_code.apply(lambda x:x[3:])
angle = angle.drop('angle_code', axis=1)
match4 = pd.merge(match3, angle, how='left', left_on=['inter_no', 'phase_no', 'ring_type'],
                 right_on=['inter_no', 'phase_no', 'ring_type']).drop_duplicates()
match4

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0        175         1         A        8       남       북       179       004
1        175         1         B        4       북       남       003       176
2        175         2         A        7       북       동       001       095
3        175         2         B        3       남       서       179       270
4        175         3         A        6       동       서       090       270
5        175         3         B        1       동       남       090       180
6        175         4         A        5       서       북       268       000
7        175         4         B        2       서       동       270       090
8        176         1         A        8       남       북       180       000
9        176         1         B        4       북       남       359       180
10       176         2         A        8       남       북       180       000
11       176         2         B        3       남       서       180       270
12       176         3         A        5       서       북       270       356
13       176         3         B       18     NaN     NaN       NaN       NaN
14       177         1         A        8       남       북       180       000
15       177         1         B        4       북       남       001       176
16       177         2         A        7       북       동       000       090
17       177         2         B        3       남       서       179       270
18       177         3         A       17     NaN     NaN       NaN       NaN
19       177         3         B       18     NaN     NaN       NaN       NaN
20       177         4         A        5       서       북       268       000
21       177         4         B        1       동       남       090       180
22       178         1         A        8       남       북       180       000
23       178         1         B        4       북       남       000       180
24       178         2         A        7       북       동       000       090
25       178         2         B        3       남       서       180       270
26       178         3         A        5       서       북       270       000
27       178         3         B        2       서       동       270       090
28       178         4         A        6       동       서       090       270
29       178         4         B        1       동       남       090       180
30       201         1         A        8       남       북       180       000
31       201         1         B        3       남       서       180       270
32       201         2         A        5       서       북       270       000
33       201         2         B        2       서       동       270       090
34       201         3         A        6       동       서       090       270
35       201         3         B        2       서       동       270       090
36       201         4         A        6       동       서       090       270
37       201         4         B        1       동       남       090       180
38       201         5         A        7       북       동       000       090
39       201         5         B        4       북       남       000       180
40       202         1         A        6       동       서       090       270
41       202         1         B        2       서       동       270       090
42       202         2         A       17     NaN     NaN       NaN       NaN
43       202         2         B       18     NaN     NaN       NaN       NaN
44       206         1         A        8       남       북       180       000
45       206         1         B        4       북       남       000       180
46       206         2         A       17     NaN     NaN       NaN       NaN
47       206         2         B       18     NaN     NaN       NaN       NaN
48       206         3         A        8       남       북       180       000
49       206         3         B        4       북       남       000       180
50       206         4    

In [6]:
# [네트워크], [교차로-노드 매칭], [교차로정보] 불러오기
net = sumolib.net.readNet('../../Data/networks/SN_sample.net.xml')
inter_node = pd.read_csv('../../Data/tables/inter_node.csv', index_col=0)
inter_info = pd.read_csv('../../Data/tables/inter_info.csv', index_col=0)

inter_node1 = inter_node[inter_node.inter_type == 'parent'].drop('inter_type', axis=1)
inter_info1 = inter_info[['inter_no', 'inter_lat', 'inter_lon']]
inter = pd.merge(inter_node1, inter_info1, how='left', left_on=['inter_no'],
                 right_on=['inter_no']).drop_duplicates()

inter2node = dict(zip(inter['inter_no'], inter['node_id']))

match5 = match4.copy()
# 진입진출ID 매칭
for index, row in match5.iterrows():
    node_id = inter2node[row.inter_no]
    node = net.getNode(node_id)
    # 교차로의 모든 (from / to) edges
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    # 교차로의 모든 (from / to) directions
    inc_dirs = []
    for inc_edge in inc_edges:
        start = inc_edge.getShape()[-2]
        end = inc_edge.getShape()[-1]
        inc_dir = np.array(end) - np.array(start)
        inc_dir = inc_dir / (inc_dir ** 2).sum() ** 0.5
        inc_dirs.append(inc_dir)
    out_dirs = []
    for out_edge in out_edges:
        start = out_edge.getShape()[0]
        end = out_edge.getShape()[1]
        out_dir = np.array(end) - np.array(start)
        out_dir = out_dir / (out_dir ** 2).sum() ** 0.5
        out_dirs.append(out_dir)
    # 진입각, 진출각 불러오기
    if not pd.isna(row.inc_angle):
        inc_angle = int(row.inc_angle)
        out_angle = int(row.out_angle)
        # 방위각을 일반각으로 가공, 라디안 변환, 단위벡터로 변환
        inc_angle = (-90 - inc_angle) % 360
        inc_angle = inc_angle * np.pi / 180.
        inc_dir_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
        out_angle = (90 - out_angle) % 360
        out_angle = out_angle * np.pi / 180.
        out_dir_true = np.array([np.cos(out_angle), np.sin(out_angle)])
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_dir, inc_dir_true) for inc_dir in inc_dirs]).argmax()
        out_index = np.array([np.dot(out_dir, out_dir_true) for out_dir in out_dirs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id   = out_edges[out_index].getID()
        match5.at[index, 'inc_edge'] = inc_edge_id
        match5.at[index, 'out_edge'] = out_edge_id
match5['node_id'] = match5['inter_no'].map(inter2node)
match5 = match5.sort_values(by=['inter_no','phase_no','ring_type']).reset_index(drop=True)
match5

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
5        175         3         B        1       동       남       090       180   
6        175         4         A        5       서       북       268       000   
7        175         4         B        2       서       동       270       090   
8        176         1         A        8       남       북       180       000   
9        176         1         B        4       북       남       359       180   
10       176         2         A        8       남       북       180       000   
11       176         2         B        3       남       서       180       270   
12       176         3         A        5       서       북       270       356   
13       176         3         B       18     NaN     NaN       NaN       NaN   
14       177         1         A        8       남       북       180       000   
15       177         1         B        4       북       남       001       176   
16       177         2         A        7       북       동       000       090   
17       177         2         B        3       남       서       179       270   
18       177         3         A       17     NaN     NaN       NaN       NaN   
19       177         3         B       18     NaN     NaN       NaN       NaN   
20       177         4         A        5       서       북       268       000   
21       177         4         B        1       동       남       090       180   
22       178         1         A        8       남       북       180       000   
23       178         1         B        4       북       남       000       180   
24       178         2         A        7       북       동       000       090   
25       178         2         B        3       남       서       180       270   
26       178         3         A        5       서       북       270       000   
27       178         3         B        2       서       동       270       090   
28       178         4         A        6       동       서       090       270   
29       178         4         B        1       동       남       090       180   
30       201         1         A        8       남       북       180       000   
31       201         1         B        3       남       서       180       270   
32       201         2         A        5       서       북       270       000   
33       201         2         B        2       서       동       270       090   
34       201         3         A        6       동       서       090       270   
35       201         3         B        2       서       동       270       090   
36       201         4         A        6       동       서       090       270   
37       201         4         B        1       동       남       090       180   
38       201         5         A        7       북       동       000       090   
39       201         5         B        4       북       남       000       180   
40       202         1         A        6       동       서       090       270   
41       202         1         B        2       서       동       270       090   
42       202         2         A       17     NaN     NaN       NaN       NaN   
43       202         2         B       18     NaN     NaN       NaN       NaN   
44       206         1         A        8       남       북       180       000   
45       206         1         B        4       북       남       000       180   
46       206         2         A       17     NaN     NaN       NaN       NaN   
47       206         2         B       18     NaN     NaN       NaN       NaN   
48       206         3         A   

In [7]:
# 유턴/연동교차로에 대하여 진입ID, 진출ID 부여
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))

uturn = pd.read_csv('../../Data/tables/child_uturn.csv')
coord = pd.read_csv('../../Data/tables/child_coord.csv')

child_ids = inter_node[inter_node.inter_type=='child'].node_id.unique()
ch2pa = {} # child to parent
for child_id in child_ids:
    parent_no = inter_node[inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = inter_node[inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향
u_ids = uturn.child_id.unique()
u_ids

array(['u00', 'u20', 'u30', 'u31', 'u32', 'u60'], dtype=object)

In [8]:
# 유턴/연동교차로에 대하여 진입ID, 진출ID 부여
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))

uturn = pd.read_csv('../../Data/tables/child_uturn.csv')
coord = pd.read_csv('../../Data/tables/child_coord.csv')
child_ids = inter_node[inter_node.inter_type=='child'].node_id.unique()
ch2pa = {} # child to parent
for child_id in child_ids:
    parent_no = inter_node[inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = inter_node[inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향
u_ids = uturn.child_id.unique()
# 각 child uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    ind = directions.index(direction)
    if condition == "좌회전시":
        print(child_id, parent_id, condition, direction)
        inc_dire = direction
        out_dire_A = out_dire_B = directions[(ind + 2) % len(directions)]
    elif condition == "직진시":
        print(child_id, parent_id, condition, direction)
        inc_dire = direction
        out_dire_A = out_dire_B = directions[(ind + 4) % len(directions)]
    elif condition == "직좌시":
        print(child_id, parent_id, condition, direction)
        inc_dire = direction
        out_dire_A = directions[(ind + 2) % len(directions)]
        out_dire_B = directions[(ind + 4) % len(directions)]
    elif condition == "보행신호시":
        print(child_id, parent_id, condition, direction)
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire_A = directions[(ind - 2) % len(directions)]
        out_dire_B = directions[(ind - 2) % len(directions)]
    cmatch = match5.copy()[match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan
    if condition == '직좌시':
        ap = cmatch[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A)].phase_no.iloc[0]
        bp = cmatch[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B)].phase_no.iloc[0]
        # 직진과 좌회전이 같은 현시에 있는 경우에만 (inc_edge_id, out_edge_id)를 부여한다.
        if ap == bp:
            cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
            cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    elif condition == '보행신호시':
        cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    else:
        cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
        cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), 'move_no'] = 19
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), 'move_no'] = 19
    display(cmatch)
    cmatches.append(cmatch)

# 각 child coordination node에 대하여 (inc_edge_id, out_edge_id) 부여
coord['inter_no'] = coord['parent_id'].map(node2inter)
coord = coord.rename(columns={'child_id':'node_id'})
coord[['inc_dir', 'out_dir', 'inc_angle','out_angle']] = np.nan
coord['move_no'] = 20
coord = coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dir', 'out_dir', 'inc_angle','out_angle', 'inc_edge', 'out_edge', 'node_id']]
# display(coord)
cmatches = pd.concat(cmatches)
display(coord)
match6 = pd.concat([match5, cmatches, coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
match6.to_csv('../../Data/tables/matching/match6.csv')
display(match6)

u00 i0 좌회전시 북


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A       19       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   
5       175         3         B        1       동       남       090       180   
6       175         4         A        5       서       북       268       000   
7       175         4         B        2       서       동       270       090   

       inc_edge         out_edge node_id  
0           NaN              NaN     u00  
1           NaN              NaN     u00  
2  571500487_02  571500487_01.32     u00  
3           NaN              NaN     u00  
4           NaN              NaN     u00  
5           NaN              NaN     u00  
6           NaN              NaN     u00  
7           NaN              NaN     u00

u20 i2 보행신호시 북


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       177         1         A        8       남       북       180       000   
1       177         1         B        4       북       남       001       176   
2       177         2         A        7       북       동       000       090   
3       177         2         B        3       남       서       179       270   
4       177         3         A       17     NaN     NaN       NaN       NaN   
5       177         3         B       18     NaN     NaN       NaN       NaN   
6       177         4         A        5       서       북       268       000   
7       177         4         B        1       동       남       090       180   

          inc_edge      out_edge node_id  
0              NaN           NaN     u20  
1              NaN           NaN     u20  
2              NaN           NaN     u20  
3              NaN           NaN     u20  
4  571542810_01.51  571542810_02     u20  
5              NaN           NaN     u20  
6              NaN           NaN     u20  
7              NaN           NaN     u20

u30 i3 보행신호시 북


...

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       178         1         A        8       남       북       180       000   
1       178         1         B       19       북       남       000       180   
2       178         2         A        7       북       동       000       090   
3       178         2         B        3       남       서       180       270   
4       178         3         A        5       서       북       270       000   
5       178         3         B        2       서       동       270       090   
6       178         4         A        6       동       서       090       270   
7       178         4         B        1       동       남       090       180   

       inc_edge       out_edge node_id  
0           NaN            NaN     u32  
1  571540303_02  -571540303_02     u32  
2           NaN            NaN     u32  
3           NaN            NaN     u32  
4           NaN            NaN     u32  
5           NaN            NaN     u32  
6           NaN            NaN     u32  
7           NaN            NaN     u32

u60 i6 직좌시 서


inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       210         1         A        6       동       서       090       270   
1       210         1         B       18     NaN     NaN       NaN       NaN   
2       210         2         A       19       서       북       268       000   
3       210         2         B       19       서       동       270       090   
4       210         3         A        7       북       동       359       090   
5       210         3         B        4       북       남       000       180   
6       210         4         A        8       남       북       180       000   
7       210         4         B        3       남       서       180       270   

       inc_edge       out_edge node_id  
0           NaN            NaN     u60  
1           NaN            NaN     u60  
2  571500535_02  -571500535_02     u60  
3  571500535_02  -571500535_02     u60  
4           NaN            NaN     u60  
5           NaN            NaN     u60  
6           NaN            NaN     u60  
7           NaN            NaN     u60

inter_no  phase_no ring_type  move_no  inc_dir  out_dir  inc_angle  \
0       178         1         A       20      NaN      NaN        NaN   
1       178         1         B       20      NaN      NaN        NaN   
2       178         2         A       20      NaN      NaN        NaN   
3       178         2         B       20      NaN      NaN        NaN   
4       178         3         A       20      NaN      NaN        NaN   
5       178         3         B       20      NaN      NaN        NaN   
6       178         4         A       20      NaN      NaN        NaN   
7       178         4         B       20      NaN      NaN        NaN   

   out_angle         inc_edge          out_edge node_id  
0        NaN              NaN               NaN     c30  
1        NaN              NaN               NaN     c30  
2        NaN     571542116_01  -571542116_02.96     c30  
3        NaN  571542116_02.96  571542116_02.164     c30  
4        NaN     571542116_01  -571542116_02.96     c30  
5        NaN  571542116_02.96  571542116_02.164     c30  
6        NaN     571542116_01  -571542116_02.96     c30  
7        NaN  571542116_02.96  571542116_02.164     c30

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B       19       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge       out_edge node_id  
0   -571542797_02   571500487_01      i0  
1   -571500487_01   571542797_02      i0  
2   -571500487_01   571545870_01      i0  
3   -571542797_02   571510153_01      i0  
4    571545870_02   571510153_01      i0  
..            ...            ...     ...  
3    571500535_02  -571500535_02     u60  
4             NaN            NaN     u60  
5             NaN            NaN     u60  
6             NaN            NaN     u60  
7             NaN            NaN     u60  

[116 rows x 11 columns]

In [9]:
# 이동류 매칭
# 각 교차로에 대하여, 가능한 모든 이동류(1~18, 21)에 대한 진입·진출엣지ID를 지정한다.
# 모든 이동류에 대해 지정하므로, 시차제시 이전과 다른 이동류가 등장하더라도 항상 진입·진출 엣지 ID를 지정할 수 있다.
match7 = match6.copy()
match7 = match7[['inter_no', 'move_no', 'inc_dir', 'out_dir', 'inc_edge', 'out_edge', 'node_id']]

parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
child_ids = sorted(inter_node[inter_node.inter_type=='child'].node_id.unique())

# (1) 가능한 (진입방향, 진출방향) 목록
flows = nema.dropna().apply(lambda row: (row['inc_dir'], row['out_dir']), axis=1).tolist()
# (2) 각 교차로별 방향 목록 : pdires (possible directions)
pdires = {}
for node_id in parent_ids:
    dires = match7[match7.node_id == node_id][['inc_dir','out_dir']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    pdires[node_id] = dires
# (3) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id (incoming direction to incoming edge_id)
inc2id = {}
for node_id in parent_ids:
    for inc_dir in pdires[node_id]:
        df = match7[(match7.node_id==node_id) & (match7.inc_dir==inc_dir)]
        inc2id[(node_id, inc_dir)] = df.inc_edge.iloc[0]
# (4) 각 (교차로, 진출방향) 별 진출id 목록 : out2id (outgoing direction to outgoing edge_id)
out2id = {}
for node_id in parent_ids:
    for out_dir in pdires[node_id]:
        df = match7[(match7.node_id==node_id) & (match7.out_dir==out_dir)]
        out2id[(node_id, out_dir)] = df.out_edge.iloc[0]
# (5) 각 교차로별 가능한 (진입방향, 진출방향) 목록 : pflow (possible flows)
pflow = {}
for node_id in parent_ids:
    pflow[node_id] = [flow for flow in flows if set(flow).issubset(pdires[node_id])]
# (6) 가능한 이동류에 대하여 진입id, 진출id 배정 : matching
node2inter = dict(zip(match7['node_id'], match7['inter_no']))
dires_right = ['북', '서', '남', '동', '북'] # ex (북, 서), (서, 남) 등은 우회전 flow
matching = []
for node_id in parent_ids:
    inter_no = node2inter[node_id]
    # 좌회전과 직진(1 ~ 16)
    for (inc_dir, out_dir) in pflow[node_id]:
        move_no = nema[(nema.inc_dir==inc_dir) & (nema.out_dir==out_dir)].move_no.iloc[0]
        inc_edge = inc2id[(node_id, inc_dir)]
        out_edge = out2id[(node_id, out_dir)]
        new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[move_no],
                                'inc_dir':[inc_dir], 'out_dir':[out_dir],
                                'inc_edge':[inc_edge], 'out_edge':[out_edge], 'node_id':[node_id]})
        matching.append(new_row)
    # 보행신호(17), 전적색(18)
    new_row = pd.DataFrame({'inter_no':[inter_no] * 2, 'move_no':[17, 18],
                            'inc_dir':[None]*2, 'out_dir':[None]*2,
                            'inc_edge':[None]*2, 'out_edge':[None]*2, 'node_id':[node_id]*2})
    matching.append(new_row)
    # 신호우회전(21)
    for d in range(len(dires_right)-1):
        inc_dir = dires_right[d]
        out_dir = dires_right[d+1]
        if {inc_dir, out_dir}.issubset(pdires[node_id]):
            inc_edge = inc2id[(node_id, inc_dir)]
            out_edge = out2id[(node_id, out_dir)]
            new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[21],
                                    'inc_dir':[inc_dir], 'out_dir':[out_dir],
                                    'inc_edge':[inc_edge], 'out_edge':[out_edge], 'node_id':[node_id]})
            matching.append(new_row)
matching.append(match7[match7.node_id.isin(child_ids)])
matching = pd.concat(matching)
matching = matching.dropna().sort_values(by=['inter_no', 'node_id', 'move_no']).reset_index(drop=True)
matching['move_no'] = matching['move_no'].astype(int)
matching.to_csv('../../Data/tables/matching/matching.csv')
display(matching)

inter_no  move_no inc_dir out_dir          inc_edge      out_edge node_id
0        175        1       동       남      571545870_02  571542797_02      i0
1        175        2       서       동      571510153_02  571545870_01      i0
2        175        3       남       서     -571542797_02  571510153_01      i0
3        175        4       북       남     -571500487_01  571542797_02      i0
4        175        5       서       북      571510153_02  571500487_01      i0
..       ...      ...     ...     ...               ...           ...     ...
69       210        8       남       북      571500585_02  571511538_01      i6
70       210       21       북       서  571511538_02.121  571500535_01      i6
71       210       21       서       남   571500535_02.18  571500585_01      i6
72       210       21       남       동      571500585_02  571542115_01      i6
73       210       21       동       북     -571542115_01  571511538_01      i6

[74 rows x 7 columns]

# B. 5초 간격으로 이동류번호 수집

In [10]:
# 5초 단위로 이동류번호 저장 및 신호이력에서 유닉스시각 가져와서 표시, 한시간동안의 데이터만 보관
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fsecs = range(midnight, next_day, 5) # fsecs : unix time by Five SECondS
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
# time2move = dict(zip(fsecs,moves)) # move : 어느 순간의 이동류정보
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)

time2movement = {} # movement : 어느 순간의, 그 순간으로부터 한시간 동안의 (교차로번호 + 현시별이동류번호 + 시작시간)
# - 아래 절차를 5초마다 반복
for fsec in tqdm(fsecs): # fsec : unix time by Five SECond
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    # move = time2move[fsec]
    move = pd.read_csv(f'../../Data/tables/moves/move_{fsec}.csv', index_col=0)
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로변호, 종료유닉스타임)만 수집 : B
    recent_histories = [group.iloc[-1:] for _, group in history[history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들
    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    move = move.drop_duplicates()
    # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        if isinstance(movement, pd.DataFrame): # movement가 존재할 경우 그걸 그대로 씀.
            pass
        else: 
            movement = pd.DataFrame()
    except NameError: # movement가 존재하지 않는 경우 생성
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - 3600을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - 3600]
    movement = movement.sort_values(by=['start_unix','inter_no','phas_A','phas_B']).reset_index(drop=True)

    time2movement[fsec] = movement
    movement.to_csv(f'../../Data/tables/movements/movements_{fsec}.csv')

# 각 movement들의 길이 시각화
import matplotlib.pyplot as plt
plt.plot(fsecs, [len(time2movement[fsec]) for fsec in fsecs])
plt.close()

  0%|          | 8/17280 [00:00<04:13, 68.11it/s]

100%|██████████| 17280/17280 [04:19<00:00, 66.61it/s]


# C. 5분 간격으로 신호이력 수집 및 통합테이블 생성

In [11]:
plan = pd.read_csv('../../Data/tables/plan.csv', index_col=0)
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)

In [12]:
# split, isplit : A,B 분리 혹은 통합시 사용될 수 있는 딕셔너리
splits = {} # splits maps (inter_no, start_hour, start_minute) to split
for i, row in plan.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    cycle = row.cycle
    cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
    cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
    splits[(inter_no, start_hour, start_minute)] = {} # split maps (phas_A, phas_B) to k
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            k += 1
        phas_A = new_phas_A
        phas_B = new_phas_B
        splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k

isplits = {} # the inverse of splits
for i in splits:
    isplits[i] = {splits[i][k]:k for k in splits[i]} # isplit maps k to (phas_A, phas_B)

# timetable
timetable = plan[['start_hour', 'start_minute']].drop_duplicates()
timetable['start_seconds'] = midnight + timetable['start_hour'] * 3600 + timetable['start_minute'] * 60
timetable

start_hour  start_minute  start_seconds
0           0             0     1704380400
1           7             0     1704405600
2           9             0     1704412800
3          18            30     1704447000

In [13]:
m = 200
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
present_time = fmins[m] # 현재시점
print(datetime.fromtimestamp(present_time))

# 1. 조회시점의 유닉스 타임 이전의 신호이력 수집
rhistory = history.copy() # recent history
rhistory = rhistory[(rhistory.end_unix < present_time)]
# 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
# - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
for i, row in rhistory.iterrows():
    inter_no = row.inter_no
    end_unix = row.end_unix
    elapsed_time = row[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]].sum() // 2 # 현시시간 합
    # 이전 유닉스 존재하지 않음 : 현시시간 합의 차
    start_unix = end_unix - elapsed_time
    pre_rows = history[:i] # previous rows
    if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
        pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
        # 이전 유닉스 존재, abs < 10 : 이전 유닉스
        if abs(pre_unix - start_unix) < 10:
            start_unix = pre_unix
        # 이전 유닉스 존재, abs >=10 : 현시시간 합의 차
        else:
            pass
    rhistory.loc[i, 'start_unix'] = start_unix 
rhistory[rhistory.isna()] = 0
rhistory['start_unix'] = rhistory['start_unix'].astype(int)
rhistory[['inter_no', 'start_unix', 'cycle']][rhistory.inter_no==175]
rhistory = rhistory[['inter_no', 'start_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle']]
inter_no = 201

2024-01-05 16:40:00


In [14]:
def calculate_DS(rhist, curr_unix):
    ghour_lt_curr_unix = hours[hours <= curr_unix].max() # the greatest hour less than (or equal to) curr_unix
    start_unixes = rhist.start_unix.unique()
    start_unixes_lt_ghour = np.sort(start_unixes[start_unixes < ghour_lt_curr_unix]) # start unixes less than ghour_lt_curr_unix
    # 기준유닉스(base_unix) : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 start_unix
    if list(start_unixes_lt_ghour):
        base_unix = start_unixes_lt_ghour[-5]
    # start_unixes_lt_ghour가 비었을 경우에는 맨 앞 start_unix로 base_unix를 지정
    else:
        base_unix = rhist.start_unix.min()
    D_n = curr_unix - base_unix
    S_n_durs = rhist[(rhist.start_unix > base_unix) & (rhist.start_unix <= curr_unix)] \
        [[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
    S_n = S_n_durs.values.sum() // 2
    return D_n, S_n

In [15]:
inter_no = 202
# 2-1. 참값 판단 프로세스
hours = np.array(range(midnight, next_day + 1, 3600)) # 정각에 해당하는 시각들 목록

rhist = rhistory.copy()[rhistory.inter_no==inter_no]
rhist = rhist.drop_duplicates(subset=['start_unix']).reset_index(drop=True)

# D_n 및 S_n 값 정의
rhist['D_n'] = 0 # D_n : 시간차이
rhist['S_n'] = 0 # S_n : 현시시간합
for n in range(len(rhist)):
    curr_unix = rhist.iloc[n].start_unix # current start_unix
    rhist.loc[n, ['D_n', 'S_n']] = calculate_DS(rhist, curr_unix)

# 결측 및 이상치 처리
prev_unix = rhist.loc[0, 'start_unix'] # previous start_unix
curr_unix = rhist.loc[1, 'start_unix'] # current start_unix
fina_unix = rhist.start_unix.max() # final start_unix
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist['start_unix'].diff()
rhist_diff[list(rhist_diff.columns)[:2]+list(rhist_diff.columns)[-4:]][65:85]

inter_no  start_unix  cycle   D_n   S_n   diff
65       202  1704389500    140  2520  2520  140.0
66       202  1704389640    140  2660  2660  140.0
67       202  1704389780    140  2800  2800  140.0
68       202  1704389920    140  2940  2940  140.0
69       202  1704390389    140  3409  3080  469.0
70       202  1704390529    140  3549  3220  140.0
71       202  1704390670    140  3690  3360  141.0
72       202  1704390810    140  3830  3500  140.0
73       202  1704390950    140  3970  3640  140.0
74       202  1704391090    140  4110  3780  140.0
75       202  1704391230    140   701   700  140.0
76       202  1704391370    140   841   840  140.0
77       202  1704391509    140   980   980  139.0
78       202  1704391650    140  1121  1120  141.0
79       202  1704391790    140  1261  1260  140.0
80       202  1704391930    140  1401  1400  140.0
81       202  1704392070    140  1541  1540  140.0
82       202  1704392211    140  1682  1680  141.0
83       202  1704392350    140  1821  1820  139.0
84       202  1704392490    140  1961  1960  140.0

In [16]:
plan.inter_no.unique()

array([175, 176, 177, 178, 201, 202, 206, 210], dtype=int64)

In [19]:
df = pd.DataFrame({'a':[1,2,3],'b':[11,22,33], 'c':[111,222,333]})
display(df)
# curr_unix = rhist.loc[n, 'start_unix']
df.loc[1,'b']


a   b    c
0  1  11  111
1  2  22  222
2  3  33  333

22

In [91]:
inter_no = 176
a, b = 70, 90
# 2-1. 참값 판단 프로세스
hours = np.array(range(midnight, next_day + 1, 3600)) # 정각에 해당하는 시각들 목록

rhist = rhistory.copy()[rhistory.inter_no==inter_no]
rhist = rhist.drop_duplicates(subset=['start_unix']).reset_index(drop=True)

# D_n 및 S_n 값 정의
rhist['D_n'] = 0 # D_n : 시간차이
rhist['S_n'] = 0 # S_n : 현시시간합
for n in range(len(rhist)):
    curr_unix = rhist.iloc[n].start_unix # current start_unix
    rhist.loc[n, ['D_n', 'S_n']] = calculate_DS(rhist, curr_unix)

rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['start_unix'].diff()
rhist_diff = rhist_diff[list(rhist_diff.columns)[:7] + list(rhist_diff.columns)[-4:]]
rhist_diff['start_dt'] = rhist_diff['start_unix'].map(lambda x:datetime.fromtimestamp(x))
display(rhist_diff[abs(rhist_diff['diff'] - rhist_diff['cycle'])>10])
display(rhist_diff[a:b])

# 이전시각, 현재시각
prev_unix = rhist.loc[0, 'start_unix'] # previous start_unix
curr_unix = rhist.loc[1, 'start_unix'] # current start_unix

# rhist의 마지막 행에 도달할 때까지 반복
while True:
    n = rhist[rhist.start_unix==curr_unix].index[0]
    cycle = rhist.loc[n, 'cycle']
    D_n = rhist.loc[n, 'D_n']
    S_n = rhist.loc[n, 'S_n']
    # 참값인 경우
    if (abs(D_n - S_n) <= 5):
        pass
    # 참값이 아닌 경우
    else:
        # 2-1-1. 결측치 처리 : 인접한 두 start_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단, 신호계획의 현시시간으로 "대체"
        if curr_unix - prev_unix >= 2 * cycle:
            # prev_unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
            # (curr_unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
            new_rows = []
            while curr_unix - prev_unix > cycle:
                prev_unix += cycle
                # 신호 계획(prow) 불러오기
                start_seconds = np.array(timetable.start_seconds)
                idx = (start_seconds <= prev_unix).sum() - 1
                start_hour = timetable.iloc[idx].start_hour
                start_minute = timetable.iloc[idx].start_minute
                prow = plan.copy()[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                # prow에서 필요한 부분을 rhist에 추가
                prow['start_unix'] = prev_unix
                prow = prow.drop(['start_hour', 'start_minute', 'offset'], axis=1)
                cycle = prow.iloc[0].cycle
                rhist = pd.concat([rhist, prow])
                rhist = rhist.sort_values(by='start_unix').reset_index(drop=True)
                n += 1

        # 2-1-2. 이상치 처리 : 비율에 따라 해당 행을 "삭제"(R_n <= 0.5) 또는 "조정"(R_n > 0.5)한다
        R_n = (curr_unix - prev_unix) / cycle # R_n : 비율
        # R_n이 0.5보다 작거나 같으면 해당 행을 삭제
        if R_n <= 0.5:
            rhist = rhist.drop(index=n).reset_index(drop=True)
            # 행삭제에 따른 curr_unix, R_n 재정의
            curr_unix = rhist.loc[n, 'start_unix']
            R_n = (curr_unix - prev_unix) / cycle # R_n : 비율

        # R_n이 0.5보다 크면 해당 행 조정 (비율을 유지한 채로 현시시간 대체)
        if R_n > 0.5:
            # 신호 계획(prow) 불러오기
            start_seconds = np.array(timetable.start_seconds)
            idx = (start_seconds <= curr_unix).sum() - 1
            start_hour = timetable.iloc[idx].start_hour
            start_minute = timetable.iloc[idx].start_minute
            prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
            # 조정된 현시시간 (prow에 R_n을 곱하고 정수로 바꿈)
            adjusted_dur = prow.copy()[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] * R_n
            int_parts = adjusted_dur.iloc[0].apply(lambda x: int(x))
            frac_parts = adjusted_dur.iloc[0] - int_parts
            difference = round(adjusted_dur.iloc[0].sum()) - int_parts.sum()
            for _ in range(difference): # 소수 부분이 가장 큰 상위 'difference'개의 값에 대해 올림 처리
                max_frac_index = frac_parts.idxmax()
                int_parts[max_frac_index] += 1
                frac_parts[max_frac_index] = 0  # 이미 처리된 항목은 0으로 설정
            # rhist에 조정된 현시시간을 반영
            rhist.loc[n, [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] = int_parts.values
            rhist.loc[n, 'cycle'] = int_parts.sum().sum() // 2

    if n == rhist.index[-1]:
        break
    prev_unix = curr_unix
    curr_unix = rhist.loc[n+1, 'start_unix']
# rhist['start_dt'] = rhist['start_unix'].map(lambda x:datetime.fromtimestamp(x))

# 생략해도 무방할 코드
rhist = rhist.reset_index(drop=True)
rhist = rhist.sort_values(by=['start_unix'])

# D_n 및 S_n 값 재정의
for n in range(len(rhist)):
    curr_unix = rhist.iloc[n].start_unix # current start_unix
    rhist.loc[n, ['D_n', 'S_n']] = calculate_DS(rhist, curr_unix)

rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['start_unix'].diff()
rhist_diff = rhist_diff[list(rhist_diff.columns)[:7] + list(rhist_diff.columns)[-4:]]
rhist_diff['start_dt'] = rhist_diff['start_unix'].map(lambda x:datetime.fromtimestamp(x))
display(rhist_diff[a:b])

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  cycle  \
24        176  1704384054       37       73       40        0        0    150   
81        176  1704392578       37       73       40        0        0    150   
143       176  1704402004       37       73       40        0        0    150   
144       176  1704402240       37       73       40        0        0    150   
167       176  1704405690       37       93       40        0        0    170   
171       176  1704406231       37       93       40        0        0    170   
210       176  1704412860       37      103       40        0        0    180   
253       176  1704420442       37      103       40        0        0    180   
277       176  1704424600       37      103       40        0        0    180   

      D_n   S_n   diff            start_dt  
24    804   750  204.0 2024-01-05 01:00:54  
81   2078  2100  128.0 2024-01-05 03:22:58  
143   874   750  274.0 2024-01-05 06:00:04  
144  1110   900  236.0 2024-01-05 06:04:00  
167   750   770  150.0 2024-01-05 07:01:30  
171  1291  1450   31.0 2024-01-05 07:10:31  
210   851   860  169.0 2024-01-05 09:01:00  
253  1283  1440   22.0 2024-01-05 11:07:22  
277  1820  1980   20.0 2024-01-05 12:16:40

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  cycle  \
70       176  1704390950       37       73       40        0        0    150   
71       176  1704391100       37       73       40        0        0    150   
72       176  1704391250       37       73       40        0        0    150   
73       176  1704391399       37       73       40        0        0    150   
74       176  1704391550       37       73       40        0        0    150   
75       176  1704391700       37       73       40        0        0    150   
76       176  1704391850       37       73       40        0        0    150   
77       176  1704392000       37       73       40        0        0    150   
78       176  1704392151       37       73       40        0        0    150   
79       176  1704392300       37       73       40        0        0    150   
80       176  1704392450       37       73       40        0        0    150   
81       176  1704392578       37       73       40        0        0    150   
82       176  1704392728       37       73       40        0        0    150   
83       176  1704392880       37       73       40        0        0    150   
84       176  1704393030       37       73       40        0        0    150   
85       176  1704393180       37       73       40        0        0    150   
86       176  1704393330       37       73       40        0        0    150   
87       176  1704393480       37       73       40        0        0    150   
88       176  1704393630       37       73       40        0        0    150   
89       176  1704393780       37       73       40        0        0    150   

     D_n   S_n   diff            start_dt  
70  4050  4050  150.0 2024-01-05 02:55:50  
71  4200  4200  150.0 2024-01-05 02:58:20  
72   750   750  150.0 2024-01-05 03:00:50  
73   899   900  149.0 2024-01-05 03:03:19  
74  1050  1050  151.0 2024-01-05 03:05:50  
75  1200  1200  150.0 2024-01-05 03:08:20  
76  1350  1350  150.0 2024-01-05 03:10:50  
77  1500  1500  150.0 2024-01-05 03:13:20  
78  1651  1650  151.0 2024-01-05 03:15:51  
79  1800  1800  149.0 2024-01-05 03:18:20  
80  1950  1950  150.0 2024-01-05 03:20:50  
81  2078  2100  128.0 2024-01-05 03:22:58  
82  2228  2250  150.0 2024-01-05 03:25:28  
83  2380  2400  152.0 2024-01-05 03:28:00  
84  2530  2550  150.0 2024-01-05 03:30:30  
85  2680  2700  150.0 2024-01-05 03:33:00  
86  2830  2850  150.0 2024-01-05 03:35:30  
87  2980  3000  150.0 2024-01-05 03:38:00  
88  3130  3150  150.0 2024-01-05 03:40:30  
89  3280  3300  150.0 2024-01-05 03:43:00

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  cycle  \
70       176  1704390950       37       73       40        0        0    150   
71       176  1704391100       37       73       40        0        0    150   
72       176  1704391250       37       73       40        0        0    150   
73       176  1704391399       37       73       40        0        0    150   
74       176  1704391550       37       73       40        0        0    150   
75       176  1704391700       37       73       40        0        0    150   
76       176  1704391850       37       73       40        0        0    150   
77       176  1704392000       37       73       40        0        0    150   
78       176  1704392151       37       73       40        0        0    150   
79       176  1704392300       37       73       40        0        0    150   
80       176  1704392450       37       73       40        0        0    150   
81       176  1704392578       32       62       34        0        0    128   
82       176  1704392728       37       73       40        0        0    150   
83       176  1704392880       37       74       41        0        0    152   
84       176  1704393030       37       73       40        0        0    150   
85       176  1704393180       37       73       40        0        0    150   
86       176  1704393330       37       73       40        0        0    150   
87       176  1704393480       37       73       40        0        0    150   
88       176  1704393630       37       73       40        0        0    150   
89       176  1704393780       37       73       40        0        0    150   

     D_n   S_n   diff            start_dt  
70  4050  4050  150.0 2024-01-05 02:55:50  
71  4200  4200  150.0 2024-01-05 02:58:20  
72   750   750  150.0 2024-01-05 03:00:50  
73   899   900  149.0 2024-01-05 03:03:19  
74  1050  1050  151.0 2024-01-05 03:05:50  
75  1200  1200  150.0 2024-01-05 03:08:20  
76  1350  1350  150.0 2024-01-05 03:10:50  
77  1500  1500  150.0 2024-01-05 03:13:20  
78  1651  1650  151.0 2024-01-05 03:15:51  
79  1800  1800  149.0 2024-01-05 03:18:20  
80  1950  1950  150.0 2024-01-05 03:20:50  
81  2078  2078  128.0 2024-01-05 03:22:58  
82  2228  2228  150.0 2024-01-05 03:25:28  
83  2380  2380  152.0 2024-01-05 03:28:00  
84  2530  2530  150.0 2024-01-05 03:30:30  
85  2680  2680  150.0 2024-01-05 03:33:00  
86  2830  2830  150.0 2024-01-05 03:35:30  
87  2980  2980  150.0 2024-01-05 03:38:00  
88  3130  3130  150.0 2024-01-05 03:40:30  
89  3280  3280  150.0 2024-01-05 03:43:00

In [237]:
rhist[list(rhist.columns)[:7] + list(rhist.columns)[-3:]].sort_values(by=['start_unix'])[260:290]

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  cycle  \
260       177  1704421770       43       27       70       40        0    180   
261       177  1704421950       43       27       70       40        0    180   
262       177  1704422130       43       27       70       40        0    180   
263       177  1704422310       43       27       70       40        0    180   
264       177  1704422490       43       27       70       40        0    180   
265       177  1704422670       43       27       70       40        0    180   
266       177  1704422849       43       27       70       40        0    180   
267       177  1704423030       43       27       70       40        0    180   
268       177  1704423210       43       27       70       40        0    180   
269       177  1704423390       43       27       70       40        0    180   
270       177  1704423570       43       27       70       40        0    180   
271       177  1704423750       43       27       70       40        0    180   
272       177  1704423929       43       27       70       40        0    180   
273       177  1704424110       43       27       70       40        0    180   
274       177  1704424290       43       27       70       40        0    180   
275       177  1704424469       43       27       70       40        0    180   
10        177  1704424649       43       27       70       40        0    180   
10        177  1704424829       43       27       70       40        0    180   
10        177  1704425009       43       27       70       40        0    180   
10        177  1704425189       43       27       70       40        0    180   
10        177  1704425369       43       27       70       40        0    180   
10        177  1704425549       43       27       70       40        0    180   
10        177  1704425729       43       27       70       40        0    180   
10        177  1704425909       43       27       70       40        0    180   
10        177  1704426089       43       27       70       40        0    180   
10        177  1704426269       43       27       70       40        0    180   
10        177  1704426449       43       27       70       40        0    180   
10        177  1704426629       43       27       70       40        0    180   
10        177  1704426809       43       27       70       40        0    180   
10        177  1704426989       43       27       70       40        0    180   

      D_n   S_n  
260  2520  2520  
261  2700  2700  
262  2880  2880  
263  3060  3060  
264  3240  3240  
265  3420  3420  
266  3599  3600  
267  3780  3780  
268  3960  3960  
269  4140  4140  
270  4320  4320  
271   901   900  
272  1080  1080  
273  1261  1260  
274  1441  1440  
275  1620  1620  
10   1800  1620  
10   1980  1800  
10   2160  1980  
10   2340  2160  
10   2520  2340  
10   2700  2520  
10   2880  2700  
10   3060  2880  
10   3240  3060  
10   3420  3240  
10   3600  3420  
10   3780  3600  
10   3960  3780  
10   4140  3960

In [174]:
print(list(rhist.columns))
print(list(new_rows[0].columns))

['inter_no', 'start_unix', 'dura_A1', 'dura_A2', 'dura_A3', 'dura_A4', 'dura_A5', 'dura_A6', 'dura_A7', 'dura_A8', 'dura_B1', 'dura_B2', 'dura_B3', 'dura_B4', 'dura_B5', 'dura_B6', 'dura_B7', 'dura_B8', 'cycle', 'D_n', 'S_n', 'offset']
['inter_no', 'dura_A1', 'dura_A2', 'dura_A3', 'dura_A4', 'dura_A5', 'dura_A6', 'dura_A7', 'dura_A8', 'dura_B1', 'dura_B2', 'dura_B3', 'dura_B4', 'dura_B5', 'dura_B6', 'dura_B7', 'dura_B8', 'cycle', 'offset', 'start_unix']


In [ ]:
# 2-1. 참값 판단 프로세스
hours = np.array(range(midnight, next_day + 1, 3600)) # 정각에 해당하는 시각들 목록

rhist = rhistory.copy()[rhistory.inter_no==inter_no].reset_index(drop=True)

# D_n 및 S_n 정의
rhist['D_n'] = 0 # D_n : 시간차이
rhist['S_n'] = 0 # S_n : 현시시간합
for n in range(len(rhist)):
    curr_unix = rhist.iloc[n].start_unix # current start_unix
    ghour_lt_curr_unix = hours[hours <= curr_unix].max() # the greatest hour less than (or equal to) curr_unix
    start_unixes = rhist.start_unix.unique()
    start_unixes_lt_ghour = np.sort(start_unixes[start_unixes < ghour_lt_curr_unix]) # start unixes less than ghour_lt_curr_unix
    # 기준유닉스(base_unix) : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 start_unix
    if list(start_unixes_lt_ghour):
        base_unix = start_unixes_lt_ghour[-5]
    # start_unixes_lt_ghour가 비었을 경우에는 맨 앞 start_unix로 base_unix를 지정
    else:
        base_unix = rhist.start_unix.min()
    D_n = curr_unix - base_unix
    S_n_durs = rhist[(rhist.start_unix > base_unix) & (rhist.start_unix <= curr_unix)] \
        [[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
    S_n = S_n_durs.values.sum() // 2
    rhist.loc[n, ['D_n', 'S_n']] = [D_n, S_n]
rhist[list(rhist.columns[:10]) + list(rhist.columns[-2:])]

new_rows = []
# 결측 및 이상치 처리
prev_unix = rhist.loc[0, 'start_unix'] # previous start_unix
curr_unix = rhist.loc[1, 'start_unix'] # current start_unix
fina_unix = rhist.loc[-1, 'start_unix'] # final start_unix
n = rhist[rhist.start_unix==curr_unix].index
print(n)
while curr_unix <= fina_unix:
    prev_unix = rhist.loc[n-1, 'start_unix'] # current start_unix
    curr_unix = rhist.loc[n, 'start_unix'] # previous start_unix
    cycle = rhist.iloc[n].cycle
    R_n = (curr_unix - prev_unix) / cycle # R_n : 비율
    # 매 반복마다 D_n 및 S_n을 다시 정의
    ghour_lt_curr_unix = hours[hours <= curr_unix].max() # the greatest hour less than (or equal to) curr_unix
    start_unixes = rhist.start_unix.unique()
    start_unixes_lt_ghour = np.sort(start_unixes[start_unixes < ghour_lt_curr_unix]) # start unixes less than ghour_lt_curr_unix
    # 기준유닉스(base_unix) : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 start_unix
    if list(start_unixes_lt_ghour):
        base_unix = start_unixes_lt_ghour[-5]
    # start_unixes_lt_ghour가 비었을 경우에는 맨 앞 start_unix로 base_unix를 지정
    else:
        base_unix = rhist.start_unix.min()
    D_n = curr_unix - base_unix
    S_n_durs = rhist[(rhist.start_unix > base_unix) & (rhist.start_unix <= curr_unix)] \
        [[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
    S_n = S_n_durs.values.sum() // 2

    # 참값인 경우
    if (abs(D_n - S_n) <= 5):
        print(n, 'true', D_n, S_n, curr_unix - prev_unix)
        pass

    # 참값이 아닌 경우
    else:
        # print(n, 'false', D_n, S_n, curr_unix - prev_unix)
        # 2-1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
        if curr_unix - prev_unix >= 2 * cycle:
            # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
            # (다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
            while curr_unix - prev_unix > cycle:
                # print(n, 'missing_values', curr_unix - prev_unix)
                prev_unix += cycle
                # 계획된 현시시간(prow) 불러오기
                start_seconds = np.array(timetable.start_seconds)
                idx = (start_seconds <= curr_unix).sum() - 1
                start_hour = timetable.iloc[idx].start_hour
                start_minute = timetable.iloc[idx].start_minute
                prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                prow = prow.drop(['start_hour', 'start_minute'], axis=1)
                prow['start_unix'] = prev_unix
                cycle = prow.iloc[0].cycle
                new_rows.append(prow)

    n += 1
new_rows = pd.concat(new_rows)
new_rows[list(new_rows.columns)[:6] + list(new_rows.columns)[-2:]]

In [117]:
rhist_diff = rhist.copy()
rhist_diff['diff'] = rhist_diff['start_unix'].diff()
rhist_diff[rhist_diff['diff'] - rhist_diff['cycle'] > 10]

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  \
155       177  1704403768       36       20       68       26        0   
276       177  1704432930       43       27       70       40        0   

     dura_A6  dura_A7  dura_A8  ...  dura_B3  dura_B4  dura_B5  dura_B6  \
155        0        0        0  ...       68       26        0        0   
276        0        0        0  ...       70       40        0        0   

     dura_B7  dura_B8  cycle   D_n   S_n    diff  
155        0        0    150  2518  2400   268.0  
276        0        0    180  9180   900  8461.0  

[2 rows x 22 columns]

In [130]:
rhist[list(rhist.columns)[:7] + list(rhist.columns)[-3:]][270:300]

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  cycle  \
270       177  1704423570       43       27       70       40        0    180   
271       177  1704423750       43       27       70       40        0    180   
272       177  1704423929       43       27       70       40        0    180   
273       177  1704424110       43       27       70       40        0    180   
274       177  1704424290       43       27       70       40        0    180   
275       177  1704424469       43       27       70       40        0    180   
276       177  1704432930       43       27       70       40        0    180   
277       177  1704433110       43       27       70       40        0    180   
278       177  1704433290       43       27       70       40        0    180   
279       177  1704433470       43       27       70       40        0    180   
280       177  1704433650       43       27       70       40        0    180   
281       177  1704433830       43       27       70       40        0    180   
282       177  1704434011       43       27       70       40        0    180   
283       177  1704434190       43       27       70       40        0    180   
284       177  1704434370       43       27       70       40        0    180   
285       177  1704434550       43       27       70       40        0    180   
286       177  1704434729       43       27       70       40        0    180   
287       177  1704434910       43       27       70       40        0    180   
288       177  1704435090       43       27       70       40        0    180   
289       177  1704435270       43       27       70       40        0    180   
290       177  1704435450       43       27       70       40        0    180   
291       177  1704435630       43       27       70       40        0    180   
292       177  1704435810       43       27       70       40        0    180   
293       177  1704435990       43       27       70       40        0    180   
294       177  1704436170       43       27       70       40        0    180   
295       177  1704436351       43       27       70       40        0    180   
296       177  1704436530       43       27       70       40        0    180   
297       177  1704436710       43       27       70       40        0    180   
298       177  1704436890       43       27       70       40        0    180   
299       177  1704437070       43       27       70       40        0    180   

       D_n   S_n  
270   4320  4320  
271    901   900  
272   1080  1080  
273   1261  1260  
274   1441  1440  
275   1620  1620  
276   9180   900  
277   9360  1080  
278   9540  1260  
279   9720  1440  
280   9900  1620  
281  10080  1800  
282  10261  1980  
283  10440  2160  
284  10620  2340  
285    900   900  
286   1079  1080  
287   1260  1260  
288   1440  1440  
289   1620  1620  
290   1800  1800  
291   1980  1980  
292   2160  2160  
293   2340  2340  
294   2520  2520  
295   2701  2700  
296   2880  2880  
297   3060  3060  
298   3240  3240  
299   3420  3420

In [109]:
rhist[210:210+60][list(rhist.columns)[:7] + list(rhist.columns)[-3:]]

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  cycle  \
210       177  1704412780       40       25       71       34        0    170   
211       177  1704412950       43       27       70       40        0    180   
212       177  1704413130       43       27       70       40        0    180   
213       177  1704413310       43       27       70       40        0    180   
214       177  1704413489       43       27       70       40        0    180   
215       177  1704413670       43       27       70       40        0    180   
216       177  1704413850       43       27       70       40        0    180   
217       177  1704414030       43       27       70       40        0    180   
218       177  1704414210       43       27       70       40        0    180   
219       177  1704414390       43       27       70       40        0    180   
220       177  1704414570       43       27       70       40        0    180   
221       177  1704414750       43       27       70       40        0    180   
222       177  1704414930       43       27       70       40        0    180   
223       177  1704415110       43       27       70       40        0    180   
224       177  1704415290       43       27       70       40        0    180   
225       177  1704415470       43       27       70       40        0    180   
226       177  1704415650       43       27       70       40        0    180   
227       177  1704415830       43       27       70       40        0    180   
228       177  1704416010       43       27       70       40        0    180   
229       177  1704416190       43       27       70       40        0    180   
230       177  1704416370       43       27       70       40        0    180   
231       177  1704416551       43       27       70       40        0    180   
232       177  1704416730       43       27       70       40        0    180   
233       177  1704416911       43       27       70       40        0    180   
234       177  1704417090       43       27       70       40        0    180   
235       177  1704417270       43       27       70       40        0    180   
236       177  1704417449       43       27       70       40        0    180   
237       177  1704417630       43       27       70       40        0    180   
238       177  1704417810       43       27       70       40        0    180   
239       177  1704417990       43       27       70       40        0    180   
240       177  1704418169       43       27       70       40        0    180   
241       177  1704418350       43       27       70       40        0    180   
242       177  1704418530       43       27       70       40        0    180   
243       177  1704418710       43       27       70       40        0    180   
244       177  1704418890       43       27       70       40        0    180   
245       177  1704419070       43       27       70       40        0    180   
246       177  1704419250       43       27       70       40        0    180   
247       177  1704419430       43       27       70       40        0    180   
248       177  1704419610       43       27       70       40        0    180   
249       177  1704419790       43       27       70       40        0    180   
250       177  1704419969       43       27       70       40        0    180   
251       177  1704420150       43       27       70       40        0    180   
252       177  1704420330       43       27       70       40        0    180   
253       177  1704420510       43       27       70       40        0    180   
254       177  1704420690       43       27       70       40        0    180   
255       177  1704420870       43       27       70       40        0    180   
256       177  1704421050       43       27       70       40        0    180   
257       177  1704421230       43       27       70       40        0    180   
258       177  1704421411       43  

In [71]:
m = 200
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
present_time = fmins[m] # 현재시점
print(datetime.fromtimestamp(present_time))

# (구) make_rhistory
Rhists = [] # Recent history (1시간 이내)
for inter_no in history.inter_no.unique():
    # - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
    # 1. 조회시점의 유닉스 타임 이전의 신호이력 수집
    rhistory = history.copy() # recent history
    rhistory = rhistory[(rhistory.end_unix < present_time)]
    hours = np.array(range(midnight, next_day + 1, 3600))
    rhist = rhistory.copy()[rhistory.inter_no == inter_no] # 특정한 inter_no
    rhist = rhist.reset_index(drop=True)
    new_rows = []
    # 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
    for n in range(len(rhist) - 1):
        curr_unix = rhist.iloc[n].end_unix # current end_unix
        next_unix = rhist.iloc[n+1].end_unix # next end_unix
        cycle = rhist.iloc[n].cycle
        if next_unix - curr_unix >= 2 * cycle:
            # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
            #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
            while next_unix - curr_unix > cycle:
                curr_unix += cycle
                start_seconds = np.array(timetable.start_seconds)
                idx = (start_seconds <= curr_unix).sum() - 1
                start_hour = timetable.iloc[idx].start_hour
                start_minute = timetable.iloc[idx].start_minute
                prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                prow = prow.drop(['start_hour', 'start_minute'], axis=1)
                prow['end_unix'] = curr_unix
                cycle = prow.iloc[0].cycle
                new_rows.append(prow)
    rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
    rhist = rhist.reset_index(drop=True)

    # 1-2. 이상치 처리 : 기준유닉스로부터의 시간차이와 현시시간합이 11 이상 차이나면 이상치가 발생했다고 판단
    Rhist = rhist.copy() # recent history 1704393231
    Rhist = Rhist[(Rhist.end_unix >= present_time - 3600)] # Recent history (1시간 이내)
    Rhist = Rhist.reset_index(drop=True)
    Rhist['D_n'] = 0
    Rhist['S_n'] = 0
    for n in range(len(Rhist)):
        curr_unix = Rhist.iloc[n].end_unix # current end_unix
        cycle = Rhist.iloc[n].cycle
        ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
        end_unixes = rhist.end_unix.unique()
        end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
        base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
        # D_n : 시간차이 
        D_n = curr_unix - base_unix
        ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
        # S_n : 현시시간합
        S_n = ddurations.values.sum() // 2
        Rhist.loc[n, ['D_n', 'S_n']] = [D_n, S_n]
    n = 1
    while n < len(Rhist):
        prev_unix = Rhist[Rhist.index==n-1]['end_unix'].iloc[0] # previous end_unix
        curr_unix = Rhist[Rhist.index==n]['end_unix'].iloc[0] # current end_unix
        R_n = (curr_unix - prev_unix) / cycle
        ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
        end_unixes = rhist.end_unix.unique()
        end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
        base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
        # D_n : 시간차이
        D_n = curr_unix - base_unix
        # S_n : 현시시간합
        ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
        S_n = ddurations.values.sum() // 2
        # 비율이 0.5보다 작거나 같으면 해당 행을 삭제
        if (abs(D_n - S_n) > 10) & (R_n <= 0.5):
            Rhist = Rhist.drop(index=n)
            n += 1
            # 행삭제에 따른 curr_unix, D_n, S_n 등 재정의
            if not Rhist[Rhist.index==n]['end_unix'].empty: # 마지막 행을 삭제하여 뒤의 행이 없을 때를 대비
                curr_unix = Rhist[Rhist.index==n]['end_unix'].iloc[0] # current end_unix
                R_n = (curr_unix - prev_unix) / cycle
                ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
                end_unixes = rhist.end_unix.unique()
                end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
                base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
            # D_n : 시간차이
            D_n = curr_unix - base_unix
            # S_n : 현시시간합
            ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
            S_n = ddurations.values.sum() // 2
        # 비율이 0.5보다 크면 해당 행 조정 (비율을 유지한 채로 현시시간 대체)
        if (abs(D_n - S_n) > 10) & (R_n > 0.5):
            start_seconds = np.array(timetable.start_seconds)
            idx = (start_seconds <= curr_unix).sum() - 1
            start_hour = timetable.iloc[idx].start_hour
            start_minute = timetable.iloc[idx].start_minute
            prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)].copy().reset_index(drop=True).iloc[0] # planned row
            adjusted_dur = prow[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] * R_n
            # 조정된 현시시간을 정수로 바꿈
            int_parts = adjusted_dur.apply(lambda x: int(x))
            frac_parts = adjusted_dur - int_parts
            difference = int(round(adjusted_dur.sum())) - int_parts.sum()
            # 소수 부분이 가장 큰 상위 'difference'개의 값에 대해 올림 처리
            for _ in range(difference):
                max_frac_index = frac_parts.idxmax()
                int_parts[max_frac_index] += 1
                frac_parts[max_frac_index] = 0  # 이미 처리된 항목은 0으로 설정
            Rhist.loc[n, [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] = int_parts.values
            Rhist.loc[n, 'cycle'] = int_parts.sum() // 2
        n += 1
    Rhist = Rhist.drop(columns=['offset', 'D_n', 'S_n'])
    Rhists.append(Rhist)
Rhists = pd.concat(Rhists)
Rhists = Rhists.sort_values(by=['end_unix', 'inter_no']).reset_index(drop=True)

# (구) make_histid
# 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
# - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
for i, row in rhistory.iterrows():
    # 이전 유닉스 존재하지 않음 => 현시시간 합의 차
    # 이전 유닉스 존재, abs < 10 => 이전 유닉스
    # 이전 유닉스 존재, abs >=10 => 현시시간 합의 차
    inter_no = row.inter_no
    end_unix = row.end_unix
    elapsed_time = row[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]].sum() // 2 # 현시시간 합
    start_unix = end_unix - elapsed_time
    pre_rows = history[:i] # previous rows
    if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
        pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
        if abs(pre_unix - start_unix) < 10: # abs < 10
            start_unix = pre_unix
        else: # abs >= 10
            pass
    rhistory.loc[i, 'start_unix'] = start_unix 
rhistory[rhistory.isna()] = 0
rhistory['start_unix'] = rhistory['start_unix'].astype(int)
rhistory = rhistory[['inter_no', 'start_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle']]

# 계층화된 형태로 변환
hrhistory = [] # hierarchied recent history
for i, row in rhistory.iterrows():
    inter_no = row.inter_no
    start_unix = row.start_unix

    ind = (timetable['start_seconds'] <= row.start_unix).sum() - 1
    start_hour = timetable.iloc[ind].start_hour
    start_minute = timetable.iloc[ind].start_minute
    isplit = isplits[(inter_no, start_hour, start_minute)]
    phas_As = [isplit[j][0] for j in isplit.keys()]
    phas_Bs = [isplit[j][1] for j in isplit.keys()]
    durs_A = row[[f'dura_A{j}' for j in range(1,9)]]
    durs_B = row[[f'dura_B{j}' for j in range(1,9)]]
    durations = []
    for j in range(1, len(isplit)+1):
        ja = isplit[j][0]
        jb = isplit[j][1]
        if ja == jb:
            durations.append(min(durs_A[ja-1], durs_B[jb-1]))
        else:
            durations.append(abs(durs_A[ja-1] - durs_B[ja-1]))
    new_rows = pd.DataFrame({'inter_no':[inter_no] * len(durations), 'start_unix':[start_unix] * len(durations),
                            'phas_A':phas_As, 'phas_B':phas_Bs, 'duration':durations})
    hrhistory.append(new_rows)
hrhistory = pd.concat(hrhistory)
hrhistory = hrhistory.sort_values(by = ['start_unix', 'inter_no', 'phas_A', 'phas_B']).reset_index(drop=True)

# 5초단위로 수집한 이동류정보(time2movement[present_time])와 최근 1시간 신호이력(hrhistory)을 병합
movedur = pd.merge(time2movement[present_time], hrhistory, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B']) # movements and durations
movedur = movedur.sort_values(by=['start_unix', 'inter_no', 'phas_A','phas_B'])
movedur = movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]

# 이동류 매칭 테이블에서 진입id, 진출id를 가져와서 붙임.
for i, row in movedur.iterrows():
    inter_no = row.inter_no
    start_unix = row.start_unix
    # incoming and outgoing edges A
    move_A = row.move_A
    if move_A in [17, 18]:
        inc_edge_A = np.nan
        out_edge_A = np.nan
    else:
        match_A = matching[(matching.inter_no == inter_no) & (matching.move_no == move_A)].iloc[0]
        inc_edge_A = match_A.inc_edge
        out_edge_A = match_A.out_edge
    movedur.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge_A, out_edge_A]
    # incoming and outgoing edges B
    move_B = row.move_B
    if move_B in [17, 18]:
        inc_edge_B = np.nan
        out_edge_B = np.nan
    else:
        match_B = matching[(matching.inter_no == inter_no) & (matching.move_no == move_B)].iloc[0]
        inc_edge_B = match_B.inc_edge
        out_edge_B = match_B.out_edge
    movedur.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge_B, out_edge_B]

# 이동류 컬럼 제거
movedur = movedur.drop(['move_A', 'move_B'], axis=1)

histid = movedur.copy() # history with edge ids (incoming and outgoing edge ids)
histid['node_id'] = histid['inter_no'].map(inter2node)
histid = histid[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'duration', 'inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']]
histid = histid[histid.start_unix > present_time - 3600]
# 시뮬레이션 시작시각 : 현재시각 - 600
# 시뮬레이션 종료시각 : 현재시각 - 300
# 현재시각 : present_time, PT
# PT-900 ... PT-600 ... PT-300 ... PT
histid

2024-01-05 16:40:00


inter_no node_id  start_unix  phas_A  phas_B  duration       inc_edge_A  \
0         202      i9  1704436810       1       1        46     571510152_02   
1         202      i9  1704436810       2       2       114              NaN   
2         178      i3  1704436860       1       1        38     571540304_02   
3         178      i3  1704436860       2       2        39     571556450_02   
4         178      i3  1704436860       3       3        43  571540303_02.21   
..        ...     ...         ...     ...     ...       ...              ...   
477       202      i9  1704440171       2       2       114              NaN   
478       206      i7  1704440171       1       1        45    -571511538_02   
479       206      i7  1704440171       2       2        53              NaN   
480       206      i7  1704440171       3       3        26    -571511538_02   
481       206      i7  1704440171       4       4        26              NaN   

        out_edge_A       inc_edge_B       out_edge_B  
0    -571510152_01     571510152_01  571510152_01.65  
1              NaN              NaN              NaN  
2     571556450_01     571556450_02     571540304_01  
3     571500475_01     571540304_02     571540303_01  
4     571556450_01  571540303_02.21     571500475_01  
..             ...              ...              ...  
477            NaN              NaN              NaN  
478   571542073_02     571542073_01     571511538_02  
479            NaN              NaN              NaN  
480   571542073_02     571542073_01     571511538_02  
481            NaN              NaN              NaN  

[482 rows x 10 columns]

In [16]:
make_histid(50)

2024-01-05 04:10:00


inter_no node_id  start_unix  phas_A  phas_B  duration     inc_edge_A  \
0         176      i1  1704391850       1       1        37  -571542810_01   
1         176      i1  1704391850       2       2        73  -571542810_01   
2         176      i1  1704391850       3       3        40   571543469_02   
3         178      i3  1704391880       1       1        38   571540304_02   
4         178      i3  1704391880       2       2        39   571556450_02   
..        ...     ...         ...     ...     ...       ...            ...   
528       201      i8  1704395250       1       1        24  -571500569_01   
529       201      i8  1704395250       2       2        24   571500618_02   
530       201      i8  1704395250       3       3        17   571500617_02   
531       201      i8  1704395250       4       4        58   571500617_02   
532       201      i8  1704395250       5       5        17   571500583_01   

           out_edge_A       inc_edge_B    out_edge_B  
0    -571542797_02.99  571542797_02.99  571542810_01  
1    -571542797_02.99    -571542810_01  571543469_01  
2    -571542797_02.99              NaN           NaN  
3        571556450_01     571556450_02  571540304_01  
4        571500475_01     571540304_02  571540303_01  
..                ...              ...           ...  
528      571500583_02    -571500569_01  571500618_01  
529      571500583_02     571500618_02  571500617_01  
530      571500618_01     571500618_02  571500617_01  
531      571500618_01     571500617_02  571500569_01  
532      571500617_01     571500583_01  571500569_01  

[533 rows x 10 columns]

In [16]:
m = 100
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
present_time = fmins[m] # 현재시점

# 1. 신호이력 데이터 수집
rhistory = history.copy()[(history.end_unix < present_time)]
rhistory = rhistory.reset_index(drop=True)
hours = np.array(range(midnight, next_day + 1, 3600))
rhist = rhistory.copy()[rhistory.inter_no == inter_no] # 특정한 inter_no
rhist = rhist.reset_index(drop=True)
rhist['D_n'] = 0 # D_n : 시간차이
rhist['S_n'] = 0 # S_n : 현시시간합
rhist

inter_no    end_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  \
0         202  1704380540       39      101        0        0        0   
1         202  1704380680       39      101        0        0        0   
2         202  1704380820       39      101        0        0        0   
3         202  1704380960       39      101        0        0        0   
4         202  1704381100       39      101        0        0        0   
..        ...         ...      ...      ...      ...      ...      ...   
200       202  1704409679       46      114        0        0        0   
201       202  1704409840       46      114        0        0        0   
202       202  1704410000       46      114        0        0        0   
203       202  1704410160       46      114        0        0        0   
204       202  1704410320       46      114        0        0        0   

     dura_A6  dura_A7  dura_A8  ...  dura_B3  dura_B4  dura_B5  dura_B6  \
0          0        0        0  ...        0        0        0        0   
1          0        0        0  ...        0        0        0        0   
2          0        0        0  ...        0        0        0        0   
3          0        0        0  ...        0        0        0        0   
4          0        0        0  ...        0        0        0        0   
..       ...      ...      ...  ...      ...      ...      ...      ...   
200        0        0        0  ...        0        0        0        0   
201        0        0        0  ...        0        0        0        0   
202        0        0        0  ...        0        0        0        0   
203        0        0        0  ...        0        0        0        0   
204        0        0        0  ...        0        0        0        0   

     dura_B7  dura_B8  cycle  offset  D_n  S_n  
0          0        0    140     103    0    0  
1          0        0    140     103    0    0  
2          0        0    140     103    0    0  
3          0        0    140     103    0    0  
4          0        0    140     103    0    0  
..       ...      ...    ...     ...  ...  ...  
200        0        0    160     103    0    0  
201        0        0    160     103    0    0  
202        0        0    160     103    0    0  
203        0        0    160     103    0    0  
204        0        0    160     103    0    0  

[205 rows x 22 columns]

In [43]:
movement = time2movement[present_time]
max_unix = movement.start_unix.max()
min_unix = movement.start_unix.min()
print(datetime.fromtimestamp(max_unix))
print(datetime.fromtimestamp(min_unix))

2024-01-05 08:19:00
2024-01-05 07:20:20


In [25]:
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
present_time = fmins[m] # 현재시점
print(datetime.fromtimestamp(present_time))

Rhists = [] # Recent history (1시간 이내)
for inter_no in history.inter_no.unique():
    # - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
    # 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 1시간 이내인(Rhist) 데이터 수집
    rhistory = history.copy() # recent history
    rhistory = rhistory[(rhistory.end_unix < present_time)]
    hours = np.array(range(midnight, next_day + 1, 3600))
    rhist = rhistory.copy()[rhistory.inter_no == inter_no] # 특정한 inter_no
    rhist = rhist.reset_index(drop=True)
    new_rows = []
    # 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
    for n in range(len(rhist) - 1):
        curr_unix = rhist.iloc[n].end_unix # current end_unix
        next_unix = rhist.iloc[n+1].end_unix # next end_unix
        cycle = rhist.iloc[n].cycle
        if next_unix - curr_unix >= 2 * cycle:
            # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
            #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
            while next_unix - curr_unix > cycle:
                curr_unix += cycle 
                start_seconds = np.array(timetable.start_seconds)
                idx = (start_seconds <= curr_unix).sum() - 1
                start_hour = timetable.iloc[idx].start_hour
                start_minute = timetable.iloc[idx].start_minute
                prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                prow = prow.drop(['start_hour', 'start_minute'], axis=1)
                prow['end_unix'] = curr_unix
                cycle = prow.iloc[0].cycle
                new_rows.append(prow)
    rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
    rhist = rhist.reset_index(drop=True)

    # 1-2. 이상치 처리 : 기준유닉스로부터의 시간차이와 현시시간합이 11 이상 차이나면 이상치가 발생했다고 판단
    Rhist = rhist.copy() # recent history 1704393231
    Rhist = Rhist[(Rhist.end_unix >= present_time - 3600)] # Recent history (1시간 이내)
    Rhist = Rhist.reset_index(drop=True)
    Rhist['D_n'] = 0
    Rhist['S_n'] = 0
    for n in range(len(Rhist)):
        curr_unix = Rhist.iloc[n].end_unix # current end_unix
        cycle = Rhist.iloc[n].cycle
        ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
        end_unixes = rhist.end_unix.unique()
        end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
        base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
        # D_n : 시간차이
        D_n = curr_unix - base_unix
        ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
        # S_n : 현시시간합
        S_n = ddurations.values.sum() // 2
        Rhist.loc[n, ['D_n', 'S_n']] = [D_n, S_n]
    n = 1
    while n < len(Rhist):
        prev_unix = Rhist[Rhist.index==n-1]['end_unix'].iloc[0] # previous end_unix
        curr_unix = Rhist[Rhist.index==n]['end_unix'].iloc[0] # current end_unix
        R_n = (curr_unix - prev_unix) / cycle
        ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
        end_unixes = rhist.end_unix.unique()
        end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
        base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
        # D_n : 시간차이
        D_n = curr_unix - base_unix
        # S_n : 현시시간합
        ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
        S_n = ddurations.values.sum() // 2
        # 비율이 0.5보다 작거나 같으면 해당 행을 삭제
        if (abs(D_n - S_n) > 10) & (R_n <= 0.5):
            # print("lt", inter_no, curr_unix, round(R_n,2), D_n, S_n)
            # display(Rhist.iloc[n])
            Rhist = Rhist.drop(index=n)
            n += 1
            # 행삭제에 따른 curr_unix, D_n, S_n 등 재정의
            if not Rhist[Rhist.index==n]['end_unix'].empty: # 마지막 행을 삭제하여 뒤의 행이 없을 때를 대비
                curr_unix = Rhist[Rhist.index==n]['end_unix'].iloc[0] # current end_unix
                R_n = (curr_unix - prev_unix) / cycle
                ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
                end_unixes = rhist.end_unix.unique()
                end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
                base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
            # D_n : 시간차이
            D_n = curr_unix - base_unix
            # S_n : 현시시간합
            ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
            S_n = ddurations.values.sum() // 2
        # 비율이 0.5보다 크면 해당 행 조정 (비율을 유지한 채로 현시시간 대체)
        if (abs(D_n - S_n) > 10) & (R_n > 0.5):
            start_seconds = np.array(timetable.start_seconds)
            idx = (start_seconds <= curr_unix).sum() - 1
            start_hour = timetable.iloc[idx].start_hour
            start_minute = timetable.iloc[idx].start_minute
            prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)].copy().reset_index(drop=True).iloc[0] # planned row
            adjusted_dur = prow[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] * R_n
            # 조정된 현시시간을 정수로 바꿈
            int_parts = adjusted_dur.apply(lambda x: int(x))
            frac_parts = adjusted_dur - int_parts
            difference = int(round(adjusted_dur.sum())) - int_parts.sum()
            # 소수 부분이 가장 큰 상위 'difference'개의 값에 대해 올림 처리
            for _ in range(difference):
                max_frac_index = frac_parts.idxmax()
                int_parts[max_frac_index] += 1
                frac_parts[max_frac_index] = 0  # 이미 처리된 항목은 0으로 설정
            Rhist.loc[n, [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] = int_parts.values
            Rhist.loc[n, 'cycle'] = int_parts.sum() // 2
            # print("gt", inter_no, curr_unix, round(R_n,2), D_n, S_n)
        n += 1
    Rhist = Rhist.drop(columns=['offset', 'D_n', 'S_n'])
    Rhists.append(Rhist)
Rhists = pd.concat(Rhists)
Rhists = Rhists.sort_values(by=['end_unix', 'inter_no']).reset_index(drop=True)

inter_no  phas_A  phas_B  move_A  move_B  start_unix
0         201       1       1       8       3  1704406820
1         201       2       2       5       2  1704406820
2         201       3       3       6       2  1704406820
3         201       4       4       6       1  1704406820
4         201       5       5       7       4  1704406820
..        ...     ...     ...     ...     ...         ...
598       202       1       1       6       2  1704410320
599       202       2       2      17      18  1704410320
600       201       1       1       8       3  1704410340
601       201       2       2       5       2  1704410340
602       201       5       5       7       4  1704410340

[603 rows x 6 columns]

In [16]:
# split, isplit : A,B 분리 혹은 통합시 사용될 수 있는 딕셔너리
splits = {} # splits maps (inter_no, start_hour, start_minute) to split
for i, row in plan.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    cycle = row.cycle
    cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
    cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
    splits[(inter_no, start_hour, start_minute)] = {} # split maps (phas_A, phas_B) to k
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            k += 1
        phas_A = new_phas_A
        phas_B = new_phas_B
        splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k

isplits = {} # the inverse of splits
for i in splits:
    isplits[i] = {splits[i][k]:k for k in splits[i]} # isplit maps k to (phas_A, phas_B)

# timetable
timetable = plan[['start_hour', 'start_minute']].drop_duplicates()
timetable['start_seconds'] = midnight + timetable['start_hour'] * 3600 + timetable['start_minute'] * 60
timetable

start_hour  start_minute  start_seconds
0           0             0     1704380400
1           7             0     1704405600
2           9             0     1704412800
3          18            30     1704447000

In [11]:
def make_rhistory(m:int):
    '''
    input : m
     - m ranges from 0 to 287, but 0 makes an error where 288 = 86400//300
     - present_time = fmins[m] : 현재시점
     + fmins[m-2] : 시뮬레이션 시작시점
     + fmins[m-1] : 시뮬레이션 종료시점
    output : rhistory
     - recent history
     - 현재시각(present_time) 이전 1시간 동안의 신호이력에 대하여 결측치 및 이상치를 처리한 결과
     - 교차로번호(inter_no), 종료유닉스(end_unix), 현시시간(dur_Aj, dur_Bj), 주기(cycle), 옵셋(offset)
    '''
    fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
    present_time = fmins[m] # 현재시점
    print(datetime.fromtimestamp(present_time))

    Rhists = [] # Recent history (1시간 이내)
    for inter_no in history.inter_no.unique():
        # - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
        # 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 1시간 이내인(Rhist) 데이터 수집
        rhistory = history.copy() # recent history
        rhistory = rhistory[(rhistory.end_unix < present_time)]
        hours = np.array(range(midnight, next_day + 1, 3600))
        rhist = rhistory.copy()[rhistory.inter_no == inter_no] # 특정한 inter_no
        rhist = rhist.reset_index(drop=True)
        new_rows = []
        # 1-1. 결측치 처리 : 인접한 두 end_unix의 차이가 계획된 주기의 두 배보다 크면 결측이 일어났다고 판단
        for n in range(len(rhist) - 1):
            curr_unix = rhist.iloc[n].end_unix # current end_unix
            next_unix = rhist.iloc[n+1].end_unix # next end_unix
            cycle = rhist.iloc[n].cycle
            if next_unix - curr_unix >= 2 * cycle:
                # 현재 unix를 계획된 주기만큼 늘려가면서 한 행씩 채워나간다.
                #(다음 unix와의 차이가 계획된 주기보다 작거나 같아질 때까지)
                while next_unix - curr_unix > cycle:
                    curr_unix += cycle
                    start_seconds = np.array(timetable.start_seconds)
                    idx = (start_seconds <= curr_unix).sum() - 1
                    start_hour = timetable.iloc[idx].start_hour
                    start_minute = timetable.iloc[idx].start_minute
                    prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)] # planned row
                    prow = prow.drop(['start_hour', 'start_minute'], axis=1)
                    prow['end_unix'] = curr_unix
                    cycle = prow.iloc[0].cycle
                    new_rows.append(prow)
        rhist = pd.concat([rhist] + new_rows).sort_values(['end_unix'])
        rhist = rhist.reset_index(drop=True)

        # 1-2. 이상치 처리 : 기준유닉스로부터의 시간차이와 현시시간합이 11 이상 차이나면 이상치가 발생했다고 판단
        Rhist = rhist.copy() # recent history 1704393231
        Rhist = Rhist[(Rhist.end_unix >= present_time - 3600)] # Recent history (1시간 이내)
        Rhist = Rhist.reset_index(drop=True)
        Rhist['D_n'] = 0
        Rhist['S_n'] = 0
        for n in range(len(Rhist)):
            curr_unix = Rhist.iloc[n].end_unix # current end_unix
            cycle = Rhist.iloc[n].cycle
            ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
            end_unixes = rhist.end_unix.unique()
            end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
            base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
            # D_n : 시간차이
            D_n = curr_unix - base_unix
            ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
            # S_n : 현시시간합
            S_n = ddurations.values.sum() // 2
            Rhist.loc[n, ['D_n', 'S_n']] = [D_n, S_n]
        n = 1
        while n < len(Rhist):
            prev_unix = Rhist[Rhist.index==n-1]['end_unix'].iloc[0] # previous end_unix
            curr_unix = Rhist[Rhist.index==n]['end_unix'].iloc[0] # current end_unix
            R_n = (curr_unix - prev_unix) / cycle
            ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
            end_unixes = rhist.end_unix.unique()
            end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
            base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
            # D_n : 시간차이
            D_n = curr_unix - base_unix
            # S_n : 현시시간합
            ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
            S_n = ddurations.values.sum() // 2
            # 비율이 0.5보다 작거나 같으면 해당 행을 삭제
            if (abs(D_n - S_n) > 10) & (R_n <= 0.5):
                Rhist = Rhist.drop(index=n)
                n += 1
                # 행삭제에 따른 curr_unix, D_n, S_n 등 재정의
                if not Rhist[Rhist.index==n]['end_unix'].empty: # 마지막 행을 삭제하여 뒤의 행이 없을 때를 대비
                    curr_unix = Rhist[Rhist.index==n]['end_unix'].iloc[0] # current end_unix
                    R_n = (curr_unix - prev_unix) / cycle
                    ghour_lt_curr_unix = hours[hours < curr_unix].max() # the greatest hour less than curr_unix
                    end_unixes = rhist.end_unix.unique()
                    end_unixes_lt_ghour = np.sort(end_unixes[end_unixes < ghour_lt_curr_unix]) # end unixes less than ghour_lt_end_unix
                    base_unix = end_unixes_lt_ghour[-5] # 기준유닉스 : curr_unix보다 작은 hour 중에서 가장 큰 값으로부터 다섯 번째로 작은 end_unix
                # D_n : 시간차이
                D_n = curr_unix - base_unix
                # S_n : 현시시간합
                ddurations = rhist[(rhist.end_unix > base_unix) & (rhist.end_unix <= curr_unix)][[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]]
                S_n = ddurations.values.sum() // 2
            # 비율이 0.5보다 크면 해당 행 조정 (비율을 유지한 채로 현시시간 대체)
            if (abs(D_n - S_n) > 10) & (R_n > 0.5):
                start_seconds = np.array(timetable.start_seconds)
                idx = (start_seconds <= curr_unix).sum() - 1
                start_hour = timetable.iloc[idx].start_hour
                start_minute = timetable.iloc[idx].start_minute
                prow = plan[(plan.inter_no==inter_no) & (plan.start_hour==start_hour) & (plan.start_minute==start_minute)].copy().reset_index(drop=True).iloc[0] # planned row
                adjusted_dur = prow[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] * R_n
                # 조정된 현시시간을 정수로 바꿈
                int_parts = adjusted_dur.apply(lambda x: int(x))
                frac_parts = adjusted_dur - int_parts
                difference = int(round(adjusted_dur.sum())) - int_parts.sum()
                # 소수 부분이 가장 큰 상위 'difference'개의 값에 대해 올림 처리
                for _ in range(difference):
                    max_frac_index = frac_parts.idxmax()
                    int_parts[max_frac_index] += 1
                    frac_parts[max_frac_index] = 0  # 이미 처리된 항목은 0으로 설정
                Rhist.loc[n, [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]] = int_parts.values
                Rhist.loc[n, 'cycle'] = int_parts.sum() // 2
            n += 1
        Rhist = Rhist.drop(columns=['offset', 'D_n', 'S_n'])
        Rhists.append(Rhist)
    Rhists = pd.concat(Rhists)
    Rhists = Rhists.sort_values(by=['end_unix', 'inter_no']).reset_index(drop=True)
    return Rhists

In [30]:
Rhists = make_rhistory(100)
Rhists

2024-01-05 08:20:00


inter_no    end_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  \
0         201  1704406820       30       36       18       58       18   
1         177  1704406830       40       25       71       34        0   
2         210  1704406850       43       39       65       23        0   
3         175  1704406870       40       42       55       33        0   
4         176  1704406910       37       93       40        0        0   
..        ...         ...      ...      ...      ...      ...      ...   
146       175  1704410269       40       42       55       33        0   
147       176  1704410310       37       93       40        0        0   
148       178  1704410310       38       39       42       41        0   
149       202  1704410320       46      114        0        0        0   
150       201  1704410340       30       36       18       58       18   

     dura_A6  dura_A7  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  dura_B5  \
0          0        0        0       30       36       18       58       18   
1          0        0        0       40       25       71       34        0   
2          0        0        0       24       58       65       23        0   
3          0        0        0       40       42       29       59        0   
4          0        0        0       37       93       40        0        0   
..       ...      ...      ...      ...      ...      ...      ...      ...   
146        0        0        0       40       42       29       59        0   
147        0        0        0       37       93       40        0        0   
148        0        0        0       38       39       62       21        0   
149        0        0        0       46      114        0        0        0   
150        0        0        0       30       36       18       58       18   

     dura_B6  dura_B7  dura_B8  cycle  
0          0        0        0    160  
1          0        0        0    170  
2          0        0        0    170  
3          0        0        0    170  
4          0        0        0    170  
..       ...      ...      ...    ...  
146        0        0        0    170  
147        0        0        0    170  
148        0        0        0    160  
149        0        0        0    160  
150        0        0        0    160  

[151 rows x 19 columns]

In [12]:
def make_histid(m):
    fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
    present_time = fmins[m]
    rhistory = make_rhistory(m)
    # 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
    # - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
    for i, row in rhistory.iterrows():
        # 이전 유닉스 존재하지 않음 => 현시시간 합의 차
        # 이전 유닉스 존재, abs < 10 => 이전 유닉스
        # 이전 유닉스 존재, abs >=10 => 현시시간 합의 차
        inter_no = row.inter_no
        end_unix = row.end_unix
        elapsed_time = row[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]].sum() // 2 # 현시시간 합
        start_unix = end_unix - elapsed_time
        pre_rows = history[:i] # previous rows
        if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
            pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
            if abs(pre_unix - start_unix) < 10: # abs < 10
                start_unix = pre_unix
            else: # abs >= 10
                pass
        rhistory.loc[i, 'start_unix'] = start_unix
    rhistory[rhistory.isna()] = 0
    rhistory['start_unix'] = rhistory['start_unix'].astype(int)
    # # with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    # #     display(rhistory)
    rhistory = rhistory[['inter_no', 'start_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle']]

    # 계층화된 형태로 변환
    hrhistory = [] # hierarchied recent history
    for i, row in rhistory.iterrows():
        inter_no = row.inter_no
        start_unix = row.start_unix

        ind = (timetable['start_seconds'] <= row.start_unix).sum() - 1
        start_hour = timetable.iloc[ind].start_hour
        start_minute = timetable.iloc[ind].start_minute
        isplit = isplits[(inter_no, start_hour, start_minute)]
        phas_As = [isplit[j][0] for j in isplit.keys()]
        phas_Bs = [isplit[j][1] for j in isplit.keys()]
        durs_A = row[[f'dura_A{j}' for j in range(1,9)]]
        durs_B = row[[f'dura_B{j}' for j in range(1,9)]]
        durations = []
        for j in range(1, len(isplit)+1):
            ja = isplit[j][0]
            jb = isplit[j][1]
            if ja == jb:
                durations.append(min(durs_A[ja-1], durs_B[jb-1]))
            else:
                durations.append(abs(durs_A[ja-1] - durs_B[ja-1]))
        new_rows = pd.DataFrame({'inter_no':[inter_no] * len(durations), 'start_unix':[start_unix] * len(durations),
                                'phas_A':phas_As, 'phas_B':phas_Bs, 'duration':durations})
        hrhistory.append(new_rows)
    hrhistory = pd.concat(hrhistory)
    hrhistory = hrhistory.sort_values(by = ['start_unix', 'inter_no', 'phas_A', 'phas_B']).reset_index(drop=True)

    # 5초단위로 수집한 이동류정보(time2movement[present_time])와 최근 1시간 신호이력(hrhistory)을 병합
    movedur = pd.merge(time2movement[present_time], hrhistory, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B']) # movements and durations
    movedur = movedur.sort_values(by=['start_unix', 'inter_no', 'phas_A','phas_B'])
    movedur = movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]

    # 이동류 매칭 테이블에서 진입id, 진출id를 가져와서 붙임.
    for i, row in movedur.iterrows():
        inter_no = row.inter_no
        start_unix = row.start_unix
        # incoming and outgoing edges A
        move_A = row.move_A
        if move_A in [17, 18]:
            inc_edge_A = np.nan
            out_edge_A = np.nan
        else:
            match_A = matching[(matching.inter_no == inter_no) & (matching.move_no == move_A)].iloc[0]
            inc_edge_A = match_A.inc_edge
            out_edge_A = match_A.out_edge
        movedur.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge_A, out_edge_A]
        # incoming and outgoing edges B
        move_B = row.move_B
        if move_B in [17, 18]:
            inc_edge_B = np.nan
            out_edge_B = np.nan
        else:
            match_B = matching[(matching.inter_no == inter_no) & (matching.move_no == move_B)].iloc[0]
            inc_edge_B = match_B.inc_edge
            out_edge_B = match_B.out_edge
        movedur.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge_B, out_edge_B]

    # 이동류 컬럼 제거
    movedur = movedur.drop(['move_A', 'move_B'], axis=1)

    histid = movedur.copy() # history with edge ids (incoming and outgoing edge ids)
    histid['node_id'] = histid['inter_no'].map(inter2node)
    histid = histid[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'duration', 'inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']]
    histid = histid[histid.start_unix > present_time - 3600]
    # 시뮬레이션 시작시각 : 현재시각 - 600
    # 시뮬레이션 종료시각 : 현재시각 - 300
    # 현재시각 : present_time, PT
    # PT-900 ... PT-600 ... PT-300 ... PT
    return histid

In [ ]:
m = 120
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
present_time = fmins[m]
rhistory = make_rhistory(m)
# 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
# - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
for i, row in rhistory.iterrows():
    # 이전 유닉스 존재하지 않음 => 현시시간 합의 차
    # 이전 유닉스 존재, abs < 10 => 이전 유닉스
    # 이전 유닉스 존재, abs >=10 => 현시시간 합의 차
    inter_no = row.inter_no
    end_unix = row.end_unix
    elapsed_time = row[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]].sum() // 2 # 현시시간 합
    start_unix = end_unix - elapsed_time
    pre_rows = history[:i] # previous rows
    if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
        pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
        if abs(pre_unix - start_unix) < 10: # abs < 10
            start_unix = pre_unix
        else: # abs >= 10
            pass
    rhistory.loc[i, 'start_unix'] = start_unix
rhistory[rhistory.isna()] = 0
rhistory['start_unix'] = rhistory['start_unix'].astype(int)
# # with pd.option_context('display.max_rows', None, 'display.max_columns', None):
# #     display(rhistory)
rhistory = rhistory[['inter_no', 'start_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle']]

# rhistoryy = rhistory.copy()[rhistory.inter_no==175]
# rhistoryy['diff'] = rhistoryy['start_unix'].diff()

# 계층화된 형태로 변환
hrhistory = [] # hierarchied recent history
for i, row in rhistory.iterrows():
    inter_no = row.inter_no
    start_unix = row.start_unix

    ind = (timetable['start_seconds'] <= row.start_unix).sum() - 1
    start_hour = timetable.iloc[ind].start_hour
    start_minute = timetable.iloc[ind].start_minute
    isplit = isplits[(inter_no, start_hour, start_minute)]
    phas_As = [isplit[j][0] for j in isplit.keys()]
    phas_Bs = [isplit[j][1] for j in isplit.keys()]
    durs_A = row[[f'dura_A{j}' for j in range(1,9)]]
    durs_B = row[[f'dura_B{j}' for j in range(1,9)]]
    durations = []
    for j in range(1, len(isplit)+1):
        ja = isplit[j][0]
        jb = isplit[j][1]
        if ja == jb:
            durations.append(min(durs_A[ja-1], durs_B[jb-1]))
        else:
            durations.append(abs(durs_A[ja-1] - durs_B[ja-1]))
    new_rows = pd.DataFrame({'inter_no':[inter_no] * len(durations), 'start_unix':[start_unix] * len(durations),
                            'phas_A':phas_As, 'phas_B':phas_Bs, 'duration':durations})
    hrhistory.append(new_rows)
hrhistory = pd.concat(hrhistory)
hrhistory = hrhistory.sort_values(by = ['start_unix', 'inter_no', 'phas_A', 'phas_B']).reset_index(drop=True)

hrhistoryy = rhistory.copy()[rhistory.inter_no==175]
hrhistoryy['diff'] = hrhistoryy['start_unix'].diff()

# display(hrhistoryy[:60])

In [ ]:
for inter_no in sorted(plan.inter_no.unique()):
    print(inter_no)
    movement = time2movement[present_time]
    movementt = movement.copy()[movement.inter_no==inter_no]
    hrhistoryy = rhistory.copy()[rhistory.inter_no==inter_no]
    mdts = sorted(movementt.start_unix.unique())
    hdts = sorted(hrhistoryy.start_unix.unique())
    import matplotlib.pyplot as plt
    plt.scatter(mdts, [0]*len(mdts), c='b')
    plt.scatter(hdts, [1]*len(hdts), c='r')
    plt.show()
    # display(movementt)
    # display(hrhistoryy)

In [ ]:
# 5초단위로 수집한 이동류정보(time2movement[present_time])와 최근 1시간 신호이력(hrhistory)을 병합
movedur = pd.merge(time2movement[present_time], hrhistory, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B']) # movements and durations
movedur = movedur.sort_values(by=['start_unix', 'inter_no', 'phas_A','phas_B'])
movedur = movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]

# 이동류 매칭 테이블에서 진입id, 진출id를 가져와서 붙임.
for i, row in movedur.iterrows():
    inter_no = row.inter_no
    start_unix = row.start_unix
    # incoming and outgoing edges A
    move_A = row.move_A
    if move_A in [17, 18]:
        inc_edge_A = np.nan
        out_edge_A = np.nan
    else:
        match_A = matching[(matching.inter_no == inter_no) & (matching.move_no == move_A)].iloc[0]
        inc_edge_A = match_A.inc_edge
        out_edge_A = match_A.out_edge
    movedur.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge_A, out_edge_A]
    # incoming and outgoing edges B
    move_B = row.move_B
    if move_B in [17, 18]:
        inc_edge_B = np.nan
        out_edge_B = np.nan
    else:
        match_B = matching[(matching.inter_no == inter_no) & (matching.move_no == move_B)].iloc[0]
        inc_edge_B = match_B.inc_edge
        out_edge_B = match_B.out_edge
    movedur.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge_B, out_edge_B]

# 이동류 컬럼 제거
movedur = movedur.drop(['move_A', 'move_B'], axis=1)

histid = movedur.copy() # history with edge ids (incoming and outgoing edge ids)
histid['node_id'] = histid['inter_no'].map(inter2node)
histid = histid[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'duration', 'inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']]
histid = histid[histid.start_unix > present_time - 3600]
# 시뮬레이션 시작시각 : 현재시각 - 600
# 시뮬레이션 종료시각 : 현재시각 - 300
# 현재시각 : present_time, PT
# PT-900 ... PT-600 ... PT-300 ... PT

histidd = histid.copy()[histid.inter_no==175]
histidd['diff'] = histidd['start_unix'].diff()
histidd[:60]

In [18]:
make_histid(100)[:30]

2024-01-05 08:20:00


inter_no node_id  start_unix  phas_A  phas_B  duration       inc_edge_A  \
0        177      i2  1704406830       1       1        40    -571542809_01   
1        177      i2  1704406830       2       2        25     571542811_02   
2        177      i2  1704406830       3       3        71              NaN   
3        177      i2  1704406830       4       4        34    -571542809_01   
4        175      i0  1704406870       1       1        40    -571542797_02   
5        175      i0  1704406870       2       2        42    -571500487_01   
6        175      i0  1704406870       3       3        29     571545870_02   
7        175      i0  1704406870       3       4        26     571545870_02   
8        175      i0  1704406870       4       4        33     571510153_02   
9        176      i1  1704406910       1       1        37    -571542810_01   
10       176      i1  1704406910       2       2        93    -571542810_01   
11       176      i1  1704406910       3       3        40     571543469_02   
12       178      i3  1704406950       1       1        38     571540304_02   
13       178      i3  1704406950       2       2        39     571556450_02   
14       178      i3  1704406950       3       3        42  571540303_02.21   
15       178      i3  1704406950       4       4        21    -571500475_01   
16       202      i9  1704406950       1       1        46     571510152_02   
17       202      i9  1704406950       2       2       114              NaN   
18       177      i2  1704407000       1       1        40    -571542809_01   
19       177      i2  1704407000       2       2        25     571542811_02   
20       177      i2  1704407000       3       3        71              NaN   
21       177      i2  1704407000       4       4        34    -571542809_01   
22       175      i0  1704407040       1       1        40    -571542797_02   
23       175      i0  1704407040       2       2        42    -571500487_01   
24       175      i0  1704407040       3       3        29     571545870_02   
25       175      i0  1704407040       3       4        26     571545870_02   
26       175      i0  1704407040       4       4        33     571510153_02   
27       176      i1  1704407080       1       1        37    -571542810_01   
28       176      i1  1704407080       2       2        93    -571542810_01   
29       176      i1  1704407080       3       3        40     571543469_02   

          out_edge_A       inc_edge_B       out_edge_B  
0       571542811_01     571542811_02     571542809_01  
1       571542107_01    -571542809_01     571542809_01  
2                NaN              NaN              NaN  
3       571542811_01     571542107_02     571542809_01  
4       571500487_01    -571500487_01     571542797_02  
5       571545870_01    -571542797_02     571510153_01  
6       571510153_01     571545870_02     571542797_02  
7       571510153_01     571510153_02     571545870_01  
8       571500487_01     571510153_02     571545870_01  
9   -571542797_02.99  571542797_02.99     571542810_01  
10  -571542797_02.99    -571542810_01     571543469_01  
11  -571542797_02.99              NaN              NaN  
12      571556450_01     571556450_02     571540304_01  
13      571500475_01     571540304_02     571540303_01  
14      571556450_01  571540303_02.21     571500475_01  
15      571540303_01    -571500475_01     571540304_01  
16     -571510152_01     571510152_01  571510152_01.65  
17               NaN              NaN              NaN  
18      571542811_01     571542811_02     571542809_01  
19      571542107_01    -571542809_01     571542809_01  
20               NaN              NaN              NaN  
21      571542811_01     571542107_02     571542809_01  
22      571500487_01    -571500487_01     571542797_02  
23      571545870_01    -571542797_02     571510153_01  
24      571510153_01     571545870_02     571542797_02  
25      571510153_01     571510153_02     571545870_01  
26      5715004

In [ ]:
inter_no = 175
rhist = make_histid(100)
rhis = rhist.copy()[rhist.inter_no==inter_no]
rhis['diff'] = rhis['start_unix'].diff()
rhis[:60]

In [ ]:
inter_no = 175
histid = make_histid(100)
his = histid.copy()[histid.inter_no==inter_no]
his['diff'] = his['start_unix'].diff()
his[:60]

In [ ]:
for m in range(30, 288):
    print(m)
    make_histid(m).to_csv(f'../../Data/tables/histids/histids_{fmins[m]}.csv')